In [1]:
import pandas as pd 
import numpy as np
import sys
import re
import string
from string import digits
import unidecode

import nltk
from nltk.corpus import stopwords
from nltk.stem.snowball import FrenchStemmer
from nltk.tokenize import word_tokenize
from nltk.tag.stanford import StanfordPOSTagger
root_path="/opt/StanfordTagguer/"
pos_tagger = StanfordPOSTagger(root_path + "models/french.tagger", root_path + "stanford-postagger.jar",encoding='utf8') #instance de la classe StanfordPOSTagger en UTF-8
def pos_tag(sentence):
    tokens = nltk.word_tokenize(sentence) #je transforme la phrase en tokens => si vous avez un texte avec plusieurs phrases, passez d'abord par nltk pour récupérer les phrases
    tags = pos_tagger.tag(tokens) #lance le tagging
    return tags

stemmer= FrenchStemmer()
stop_words = set(stopwords.words('perso'))
stop_words.add('a')
def clean_string(sentence):
     # All char to lower case ...
    cleaned_sentence = sentence.lower() 
    
    # Remove all digits
    remove_digit = str.maketrans('', '', digits)
    cleaned_sentence=cleaned_sentence.translate(remove_digit)
    # Remove all punctuation
    translator = re.compile('[%s]' % re.escape(string.punctuation))
    cleaned_sentence=translator.sub(' ', cleaned_sentence)
    # Remove all spaces
    cleaned_sentence=' '.join(cleaned_sentence.split())
    # Remove stopwords
    tokens = word_tokenize(cleaned_sentence)
    result = [i for i in tokens if not i in stop_words]
    cleaned_sentence = ' '.join(result)
    tokens = word_tokenize(cleaned_sentence)
    typePT= pos_tag(cleaned_sentence)
    result= []
    for item in typePT:
        if item[1]=='NC' or item[1]=='NP' or item[1]=='N' or item[1]=='NPP':
            result.append(item[0])
    cleaned_sentence = ' '.join(result)
    #tokens = word_tokenize(cleaned_sentence)
   # stemmed=[]
    
    #for word in tokens:
     #   stemmed.append(stemmer.stem(word))
    #cleaned_sentence = ' '.join(stemmed)
    return cleaned_sentence




data = pd.read_csv('../data/export_articles_EGC_2004_2018.csv', delimiter='\t')

In [2]:
data_abstract_title = pd.DataFrame(columns=['authors', 'title_abstract'])    

In [3]:
for index, row in data.iterrows():
    print(round((index*100)/len(data), 2),"% / 100%", end='\r') # Print a loading bar ... 
    if str(row['abstract']) == "nan":
        data_abstract_title = data_abstract_title.append({'authors': row['authors'], 'title_abstract': clean_string(row['title'])}, ignore_index=True)
    else:
        data_abstract_title = data_abstract_title.append({'authors': row['authors'], 'title_abstract': clean_string(row['title'] + " "+ row['abstract'])}, ignore_index=True)
    
    #data_abstract_title = data_abstract_title.append({'num_doc': i, 'title_abstract': row['title'] + row['abstract']})

In [4]:
pd.set_option('display.max_rows', None)
#data_abstract_title

In [5]:
# Buid array with all authors names uniq
uniq_names = []
setUniq=set(uniq_names)
i = 0
for row in data_abstract_title.iterrows():
    athors_paper = data_abstract_title["authors"].iloc[i].split(', ')
    setAuthor=set(athors_paper)
    uniq_names = uniq_names + list(setAuthor-setUniq)
    setUniq=set(uniq_names)
    i=i+1
   

# Get number of authors
nb_authors = len(uniq_names)

nb_authors

2007

In [6]:
uniq_names

['Abdulhafiz Alkhouli',
 'Nader Hassine',
 'Claudia Marinica',
 'Julien Longhi',
 'Boris Borzic',
 'Marius Barctus',
 'Fabrice Clérot',
 'Marc Boullé',
 'Jean-Benoît Griesner',
 'Talel Abdesssalem',
 'Hubert Naacke',
 'Pierre Dosne',
 'Hafdalla Hammia',
 'Abdeljalil Elouardighi',
 'Fatima-Zahra Aazi',
 'Mohcine Maghfour',
 'Elyase Lassouli',
 'Yasmine Mesbahi',
 'Camille Pradel',
 'Damien Sileo',
 'Christophe Nicolle',
 'Marwan Batrouni',
 'Aurélie Bertaux',
 'Enrique Baca-García',
 'Romain Billot',
 'Philippe Lenca',
 'Jorge López Castroman',
 'Mark Larsen',
 'Philippe Courtet',
 'Michel Walter',
 'Sofian Berrouiguet',
 'Vincent Lemaire',
 'Oumaima Alaoui Ismaili',
 'Mohammed Ramdani',
 'Khalil Laghmari',
 'Christophe Marsala',
 'Myriam Maumy-Bertrand',
 'Pierre Gançarski',
 'Emmanuelle Claeys',
 'Fosca Giannotti',
 'Denis Maurel',
 'Jérémie Sublime',
 'Sylvain Lefebvre',
 'Jonathan Weber',
 'Germain Forestier',
 'Michel Hassenforder',
 'Bastien Latard',
 'Étienne-Cuvelier',
 'Marie-A

In [7]:
data_abstract_title_uniq = pd.DataFrame(columns=['author', 'title_abstract'])   

for name in uniq_names:
    data_abstract_title_uniq = data_abstract_title_uniq.append({'author': name, 'title_abstract': ""}, ignore_index=True)
    
    

In [8]:
#data_abstract_title_uniq


In [9]:
for i, rowi in data_abstract_title.iterrows():
    print(round((i*100)/len(data_abstract_title), 2),"% / 100%", end='\r') # Print a loading bar ... 
    athors_paper = data_abstract_title["authors"].iloc[i].split(', ')
    paper=data_abstract_title["title_abstract"].iloc[i]
    for author in athors_paper:
        data_abstract_title_uniq.loc[data_abstract_title_uniq["author"]==author,["title_abstract"]] = data_abstract_title_uniq.loc[data_abstract_title_uniq["author"]==author,["title_abstract"]]+ " " +paper

In [10]:
data_abstract_title_uniq

author  \
0                        Abdulhafiz Alkhouli   
1                              Nader Hassine   
2                           Claudia Marinica   
3                              Julien Longhi   
4                               Boris Borzic   
5                             Marius Barctus   
6                             Fabrice Clérot   
7                                Marc Boullé   
8                       Jean-Benoît Griesner   
9                          Talel Abdesssalem   
10                             Hubert Naacke   
11                              Pierre Dosne   
12                           Hafdalla Hammia   
13                    Abdeljalil Elouardighi   
14                         Fatima-Zahra Aazi   
15                          Mohcine Maghfour   
16                           Elyase Lassouli   
17                           Yasmine Mesbahi   
18                            Camille Pradel   
19                              Damien Sileo   
20                        Christophe Nicolle   
21                           Marwan Batrouni   
22                           Aurélie Bertaux   
23                       Enrique Baca-García   
24                             Romain Billot   
25                            Philippe Lenca   
26                     Jorge López Castroman   
27                               Mark Larsen   
28                          Philippe Courtet   
29                             Michel Walter   
30                        Sofian Berrouiguet   
31                           Vincent Lemaire   
32                    Oumaima Alaoui Ismaili   
33                          Mohammed Ramdani   
34                           Khalil Laghmari   
35                        Christophe Marsala   
36                     Myriam Maumy-Bertrand   
37                          Pierre Gançarski   
38                         Emmanuelle Claeys   
39                           Fosca Giannotti   
40                              Denis Maurel   
41                           Jérémie Sublime   
42                          Sylvain Lefebvre   
43                            Jonathan Weber   
44                         Germain Forestier   
45                       Michel Hassenforder   
46                            Bastien Latard   
47                          Étienne-Cuvelier   
48                        Marie-Aude-Aufaure   
49                           Santo Fortunato   
50                             Marwan Ghanem   
51                           Fabien Tarissan   
52                          Clémence Magnien   
53                           Philippe Muller   
54                          Tim Van de Cruys   
55                            Bich-Liên Doan   
56                                Julien Hay   
57                          Fabrice Popineau   
58                            Lyes Benamsili   
59                           Badre Belabbess   
60                               Jérémy Lhez   
61                              Musab Bairat   
62                              Olivier Curé   
63                           Philippe Martin   
64                                    Jun Jo   
65                             Amedeo Napoli   
66                                Alain Gély   
67                             Yassine Namir   
68                           Miguel Couceiro   
69                                 Simon Ser   
70                               Fatiha Saïs   
71                      Maguelonne Teisseire   
72                            Esther Galbrun   
73                              Mehwish Alam   
74                           Justine Reynaud   
75                         Yannick Toussaint   
76                               Lamine Diop   
77                     Cheikh Talibouya Diop   
78                              Dominique Li   
79                         Arnaud Giacometti   
80                             Arnaud Soulet   
81                             Norbert Feron   
82                              Guy Melançon   
83    

In [11]:
data_abstract_title_uniq.iloc[400]["title_abstract"]

' caractérisation apprentissage machine powerful getting experts choice calibration machine thusto assistance solution limitation currentdata characterization'

In [12]:

uniq_words = []
for index, row in data_abstract_title_uniq.iterrows():
    tokens = word_tokenize(row["title_abstract"])
    for token in tokens:
        if token not in uniq_words:
            uniq_words.append(token)

In [13]:
print(len(uniq_words))

3797


In [14]:
zero_matrix = np.zeros((len(uniq_names), len(uniq_words)))

In [15]:
# Create publication adjacency matrix 
names = [_ for _ in uniq_names]
term_freq_matrix = pd.DataFrame(zero_matrix, index=uniq_names, columns=uniq_words)

In [16]:
term_freq_matrix

citoyenne  événements  objectif  \
Abdulhafiz Alkhouli                           0.0         0.0       0.0   
Nader Hassine                                 0.0         0.0       0.0   
Claudia Marinica                              0.0         0.0       0.0   
Julien Longhi                                 0.0         0.0       0.0   
Boris Borzic                                  0.0         0.0       0.0   
Marius Barctus                                0.0         0.0       0.0   
Fabrice Clérot                                0.0         0.0       0.0   
Marc Boullé                                   0.0         0.0       0.0   
Jean-Benoît Griesner                          0.0         0.0       0.0   
Talel Abdesssalem                             0.0         0.0       0.0   
Hubert Naacke                                 0.0         0.0       0.0   
Pierre Dosne                                  0.0         0.0       0.0   
Hafdalla Hammia                               0.0         0.0       0.0   
Abdeljalil Elouardighi                        0.0         0.0       0.0   
Fatima-Zahra Aazi                             0.0         0.0       0.0   
Mohcine Maghfour                              0.0         0.0       0.0   
Elyase Lassouli                               0.0         0.0       0.0   
Yasmine Mesbahi                               0.0         0.0       0.0   
Camille Pradel                                0.0         0.0       0.0   
Damien Sileo                                  0.0         0.0       0.0   
Christophe Nicolle                            0.0         0.0       0.0   
Marwan Batrouni                               0.0         0.0       0.0   
Aurélie Bertaux                               0.0         0.0       0.0   
Enrique Baca-García                           0.0         0.0       0.0   
Romain Billot                                 0.0         0.0       0.0   
Philippe Lenca                                0.0         0.0       0.0   
Jorge López Castroman                         0.0         0.0       0.0   
Mark Larsen                                   0.0         0.0       0.0   
Philippe Courtet                              0.0         0.0       0.0   
Michel Walter                                 0.0         0.0       0.0   
Sofian Berrouiguet                            0.0         0.0       0.0   
Vincent Lemaire                               0.0         0.0       0.0   
Oumaima Alaoui Ismaili                        0.0         0.0       0.0   
Mohammed Ramdani                              0.0         0.0       0.0   
Khalil Laghmari                               0.0         0.0       0.0   
Christophe Marsala                            0.0         0.0       0.0   
Myriam Maumy-Bertrand                         0.0         0.0       0.0   
Pierre Gançarski                              0.0         0.0       0.0   
Emmanuelle Claeys                             0.0         0.0       0.0   
Fosca Giannotti                               0.0         0.0       0.0   
Denis Maurel                                  0.0         0.0       0.0   
Jérémie Sublime                               0.0         0.0       0.0   
Sylvain Lefebvre                              0.0         0.0       0.0   
Jonathan Weber                                0.0         0.0       0.0   
Germain Forestier                             0.0         0.0       0.0   
Michel Hassenforder                           0.0         0.0       0.0   
Bastien Latard                                0.0         0.0       0.0   
Étienne-Cuvelier                              0.0         0.0       0.0   
Marie-Aude-Aufaure                            0.0         0.0       0.0   
Santo Fortunato                               0.0         0.0       0.0   
Marwan Ghanem                                 0.0         0.0       0.0   
Fabien Tarissan                               0.0         0.0       0.0   
Clémence Magnien                              0.0         0.0    

In [23]:
def author_term(author,sentence, adjecency_matrix):
    allWords=word_tokenize(sentence)
    for word in allWords:
        adjecency_matrix[word][author] = adjecency_matrix[word][author] + 1
       


In [24]:
i=0
for row in data_abstract_title_uniq.iterrows():
    author=data_abstract_title_uniq["author"].iloc[i]
    abstract=data_abstract_title_uniq["title_abstract"].iloc[i]
    author_term(author,abstract,term_freq_matrix)
    i=i+1


In [25]:
term_freq_matrix

citoyenne  événements  objectif  \
Abdulhafiz Alkhouli                           1.0         2.0       1.0   
Nader Hassine                                 1.0         2.0       1.0   
Claudia Marinica                              1.0         2.0       1.0   
Julien Longhi                                 1.0         2.0       1.0   
Boris Borzic                                  1.0         2.0       1.0   
Marius Barctus                                0.0         0.0       0.0   
Fabrice Clérot                                0.0         0.0       1.0   
Marc Boullé                                   0.0         0.0       1.0   
Jean-Benoît Griesner                          0.0         0.0       0.0   
Talel Abdesssalem                             0.0         0.0       0.0   
Hubert Naacke                                 0.0         0.0       0.0   
Pierre Dosne                                  0.0         0.0       0.0   
Hafdalla Hammia                               0.0         0.0       0.0   
Abdeljalil Elouardighi                        0.0         0.0       0.0   
Fatima-Zahra Aazi                             0.0         0.0       0.0   
Mohcine Maghfour                              0.0         0.0       0.0   
Elyase Lassouli                               0.0         0.0       0.0   
Yasmine Mesbahi                               0.0         0.0       0.0   
Camille Pradel                                0.0         0.0       0.0   
Damien Sileo                                  0.0         0.0       0.0   
Christophe Nicolle                            0.0         0.0       1.0   
Marwan Batrouni                               0.0         0.0       0.0   
Aurélie Bertaux                               0.0         0.0       0.0   
Enrique Baca-García                           0.0         0.0       0.0   
Romain Billot                                 0.0         0.0       0.0   
Philippe Lenca                                0.0         0.0       0.0   
Jorge López Castroman                         0.0         0.0       0.0   
Mark Larsen                                   0.0         0.0       0.0   
Philippe Courtet                              0.0         0.0       0.0   
Michel Walter                                 0.0         0.0       0.0   
Sofian Berrouiguet                            0.0         0.0       0.0   
Vincent Lemaire                               0.0         0.0       2.0   
Oumaima Alaoui Ismaili                        0.0         0.0       0.0   
Mohammed Ramdani                              0.0         0.0       0.0   
Khalil Laghmari                               0.0         0.0       0.0   
Christophe Marsala                            0.0         3.0       0.0   
Myriam Maumy-Bertrand                         0.0         0.0       0.0   
Pierre Gançarski                              0.0         0.0       0.0   
Emmanuelle Claeys                             0.0         0.0       0.0   
Fosca Giannotti                               0.0         0.0       0.0   
Denis Maurel                                  0.0         0.0       0.0   
Jérémie Sublime                               0.0         0.0       0.0   
Sylvain Lefebvre                              0.0         0.0       0.0   
Jonathan Weber                                0.0         0.0       0.0   
Germain Forestier                             0.0         0.0       0.0   
Michel Hassenforder                           0.0         0.0       0.0   
Bastien Latard                                0.0         0.0       0.0   
Étienne-Cuvelier                              0.0         0.0       0.0   
Marie-Aude-Aufaure                            0.0         0.0       0.0   
Santo Fortunato                               0.0         0.0       0.0   
Marwan Ghanem                                 0.0         0.0       0.0   
Fabien Tarissan                               0.0         0.0       0.0   
Clémence Magnien                              0.0         0.0    

In [29]:
term_freq_matrix[."Boris Borzic"].max()

SyntaxError: invalid syntax (<ipython-input-29-fd272df57fd0>, line 1)